In [1]:
from dataloader_utils import get_conbined_permute_mnist, get_conbined_split_mnist, get_conbined_splitted_and_shuffled_mnist
from autoencoder import Autoencoder
from autoencoder_utils import *

import numpy as np
import matplotlib.pyplot as plt
import random

from tqdm.notebook import tqdm

import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import transforms

DEBUG = 1

In [8]:
# the autoencoder training
# num_train_batch is the number of batches of data to train the autoencoder
def train_ae(train_loader, num_epochs=10, num_train_batch=1):
    auto_list = {}
    group_size = len(train_loader)
    count_wrong = {}
    count_wrong_vital = []
    for v in range(10):
      counter_vital = 0
      counter = 0
      random_idx1 = random.randrange(0, group_size//2)
      the_ae = None
      taskNo1 = -1
      trained_counter = 1
      for i, data in tqdm(enumerate(train_loader), total=len(train_loader)):
          images, labels, indicies = data
          taskNo = indicies[0].item()
          if i == random_idx1:
              #initial autoencoder
              the_ae = Autoencoder(input_dims=28*28, code_dims=CODE_DIM)
              auto_list[taskNo] = the_ae
              taskNo1 = taskNo
              if count_wrong.get(taskNo1)==None: count_wrong[taskNo1] = []
              for epoch in range(NEW_AUTOENCODER_EPOCH):
                  the_ae.optimize_params(images, images)
          elif taskNo == taskNo1 and trained_counter < num_train_batch:
            trained_counter += 1
            for epoch in range(TRAIN_AUTOENCODER_EPOCH):
              the_ae.optimize_params(images, images)
      # print('trained_counter', trained_counter)
      for i, data in tqdm(enumerate(train_loader), total=len(train_loader)):
          images, labels, indicies = data
          taskNo = indicies[0].item()
          outliers = find_num_of_outliers(images, the_ae)
          if outliers <= OUTLIER_THRESHOLD:
            if taskNo != taskNo1:
              counter_vital += 1
              counter += 1
          elif taskNo1 == taskNo:
            counter += 1
      count_wrong[taskNo1].append(counter)
      count_wrong_vital.append(counter_vital)

    return count_wrong, count_wrong_vital, auto_list

In [ ]:
BATCH_SIZE = 300

OUTLIER_THRESHOLD = 0.2*BATCH_SIZE
NEW_AUTOENCODER_EPOCH = 100
TRAIN_AUTOENCODER_EPOCH = 10
CODE_DIM = 350

NUM_TASK = 5
RANDOM_SEED = np.random.randint(100)
#RANDOM_SEED = 42
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

train_loader, test_loader = get_conbined_permute_mnist(NUM_TASK, BATCH_SIZE, RANDOM_SEED)
error_rates = {
    1: [],
    2: [],
    5: [],
    10: [],
}
for x in range(10):
  for i in (1,2,5,10):
    count_wrong, count_wrong_vital, auto_list = train_ae(train_loader, num_train_batch=i)
    for t in range(NUM_TASK):
      e_mean = np.mean([0] if count_wrong.get(t)==None else count_wrong.get(t))
      if x == 0:
        error_rates[i].append(e_mean)
      else:
        error_rates[i][t] = (error_rates[i][t]*x + e_mean)/(x+1)
      print(x, i, t, error_rates)

Failed to download (trying next):
HTTP Error 503: Service Unavailable



100%|██████████| 9912422/9912422 [00:08<00:00, 1207241.87it/s]


Extracting ./MNIST/PermutedMNIST/raw/train-images-idx3-ubyte.gz to ./MNIST/PermutedMNIST/raw

Failed to download (trying next):
HTTP Error 503: Service Unavailable



100%|██████████| 28881/28881 [00:00<00:00, 130054.86it/s]


Extracting ./MNIST/PermutedMNIST/raw/train-labels-idx1-ubyte.gz to ./MNIST/PermutedMNIST/raw

Failed to download (trying next):
HTTP Error 503: Service Unavailable



...

  0%|          | 0/1000 [00:00<?, ?it/s]

  0%|          | 0/1000 [00:00<?, ?it/s]

  0%|          | 0/1000 [00:00<?, ?it/s]

  0%|          | 0/1000 [00:00<?, ?it/s]

  0%|          | 0/1000 [00:00<?, ?it/s]

[1, 3, 0, 8, 1, 25, 11, 2, 2, 20]

[1, 0, 10, 0, 6, 6, 6, 0, 0, 0]

[0, 0, 10, 5, 5, 2, 6, 10, 12, 18]



In [ ]:
for i in range(NUM_TASK):
  x = [1, 2, 5, 10]
  y = [ error_rates[v][i] for v in x ]

  plt.figure(figsize=(8, 6))
  plt.plot(x, y, marker='o', linestyle='-', color='b')
  plt.title(f'Error Rates by Number of Data Batches Trained for Task {i} of Permuted MNIST')
  plt.xlabel('Number of Batches of Data')
  plt.ylabel('Error Rate(%)')
  plt.grid(True)
  plt.xticks(x)
  plt.show()

In [ ]:
BATCH_SIZE = 320

OUTLIER_THRESHOLD = 0.1*BATCH_SIZE
NEW_AUTOENCODER_EPOCH = 200
TRAIN_AUTOENCODER_EPOCH = 20
CODE_DIM = 350

NUM_TASK = 5
RANDOM_SEED = np.random.randint(100)
#RANDOM_SEED = 42
train_loader, test_loader, idx = get_conbined_splitted_and_shuffled_mnist(NUM_TASK, BATCH_SIZE, RANDOM_SEED)

error_ratess = {
    1: [],
    2: [],
    5: [],
    10: [],
}
for x in range(10):
  for i in {1, 2, 5, 10}:
    count_wrong_split, count_wrong_vital_split, auto_list_split = train_ae(train_loader, num_train_batch=i)
    for t in range(NUM_TASK):
      e_mean = np.mean([0] if count_wrong_split.get(t)==None else count_wrong_split.get(t))
      if x == 0:
        error_ratess[i].append(e_mean)
      else:
        error_ratess[i][t] = (error_ratess[i][t]*x + e_mean)/(x+1)
      print(x, i, t, error_ratess)
      # print(f'{x} {i} Task{t} {count_wrong_split.get(t)}, {count_wrong_vital_split}, {e_mean}')

In [ ]:
for i in range(NUM_TASK):
  x = [1, 2, 5, 10]
  y = [ error_ratess[v][i]/188 for v in x ]

  plt.figure(figsize=(8, 6))
  plt.plot(x, y, marker='o', linestyle='-', color='b')
  plt.title(f'Error Rates by Number of Data Batches Trained for Task {i} of Splitted&Shuffled MNIST')
  plt.xlabel('Number of Batches of Data')
  plt.ylabel('Error Rate (%)')
  plt.grid(True)
  plt.xticks(x)
  plt.show()